# Santa Challenge | Verification and Visualization
Dennis Briner, 15.12.2020

<br>

This notebook helps to verify your solution for the [Santa Challenge](https://www.kaggle.com/c/santas-stolen-sleigh). You may run this directly in Colab or any other Jupyter environment like Jupyter Notebooks or PyCharm.

Make sure you have the data folder as described in the prerequisites. 

## Prerequisites

You'll need to upload a `gifts.csv` and a `submission.csv`

## ☝️Note
We expect the submission file to be ordered by TripId, and the stops within the trips to be in order!

Python libraries needed to run this notebook:
- Haversine
- Pandas
- Folium

In [ ]:
# Colab doesn't have haversine by default
!pip install haversine

## Methods for verification

In [ ]:
# I couldn't see an improvement in using cHaversine
from haversine import haversine

# globals
north_pole = (90, 0)
weight_limit = 1000
sleigh_weight = 10

# Returns the distance of one trip
# Input: stops (list of stops such as [[latStopA,longStopA],[latStopB,longStopB],...])
# Input: weights (list of weights such as [weightGiftA,weightGiftB,...])
def weighted_trip_length(stops, weights):
    tuples = [tuple(x) for x in stops.values]
    # adding the last trip back to north pole, with just the sleigh weight
    tuples.append(north_pole)
    weights.append(sleigh_weight)

    dist = 0.0
    prev_stop = north_pole
    prev_weight = sum(weights)
    for location, weight in zip(tuples, weights):
        dist = dist + haversine(location, prev_stop) * prev_weight
        prev_stop = location
        prev_weight = prev_weight - weight
    return dist


# Returns the distance of all trips
# Input: all_trips (Pandas DataFrame)
def weighted_reindeer_weariness(all_trips):
    uniq_trips = all_trips.TripId.unique()

    dist = 0.0
    for t in uniq_trips:
        this_trip = all_trips[all_trips.TripId == t]
        dist = dist + weighted_trip_length(this_trip[['Latitude', 'Longitude']], this_trip.Weight.tolist())

    return dist


# Checks if one trip is over the weight limit
def check_for_overweight(all_trips):
    if any(all_trips.groupby('TripId').Weight.sum() > weight_limit):
        raise Exception("One of the sleighs over weight limit!")

## Methods for visualization

In [ ]:
import folium
import random


def get_route_map(df, points_color='blue', include_home=False):
    m = folium.Map(location=[df.iloc[0]['Latitude'], df.iloc[0]['Longitude']], zoom_start=3)

    last_index = df.shape[0] - 1
    previous_point = None

    i = 0
    for index, row in df.iterrows():
        current_point = (row['Latitude'], row['Longitude'])

        if i == 0:
            color = 'green'
            if include_home:
                folium.PolyLine([[90, 0], current_point], color="green", weight=2, opacity=0.3).add_to(m)
        elif i == last_index:
            color = 'red'
        else:
            color = points_color

        tooltip = f"Tour-Point: {str(i)} Index: {str(index)}<br>Id: {row['GiftId']} Weight: {'{:.2f}'.format(row['Weight'])} <br>Lat: {'{:.2f}'.format(row['Latitude'])} Long: {'{:.2f}'.format(row['Latitude'])}"

        folium.CircleMarker(location=current_point, radius=5, color=color, fill=True,
                            tooltip=tooltip, fill_color=color).add_to(m)

        if previous_point:
            folium.PolyLine([previous_point, current_point], color="blue", weight=2, opacity=0.3).add_to(m)

        previous_point = current_point
        i += 1

    if include_home:
        folium.PolyLine([[90, 0], previous_point], color="darkred", weight=2, opacity=0.3).add_to(m)

    return m


class MapVisualizer:
    map = None

    def __init__(self):
        self._init_map()

    def add_route(self, path):
        color = "#{:06x}".format(random.randint(0, 0xFFFFFF))
        folium.PolyLine(path, color=color, weight=1).add_to(self.map)

    def _init_map(self):
        self.map = folium.Map(location=[40.52, 34.34], zoom_start=1)

    def save_map(self, save_path):
        self.map.save(save_path)

## Actually run the code

In [ ]:
import pandas as pd

submission = pd.read_csv('sample_submission.csv')
gifts = pd.read_csv('gifts.csv')
df = pd.merge(submission, gifts, how='left')
df['Position'] = list(zip(df['Latitude'],df['Longitude']))

df.head()

GiftId  TripId  ...     Weight                              Position
0   76714       0  ...   1.000000      (-72.0130020741, -98.7552337146)
1   51298       0  ...  32.467601      (-72.2676856361, -99.3184707219)
2   65147       0  ...   9.245825  (-72.50036752930001, -99.4657149377)
3   83464       0  ...  17.503786  (-72.6256184872, -99.38371066719999)
4   73928       0  ...   1.247361      (-72.6439968783, -99.2074599653)

[5 rows x 6 columns]

### Verify

In [ ]:
# Weighted Reindeer Weariness
wrw = weighted_reindeer_weariness(df)
print(wrw)
print('{:e}'.format(wrw))

13430490402.690832
1.343049e+10


In [ ]:
# No error here means all trips are legit!
print(check_for_overweight(df))

None


### Visualize

In [ ]:
visualizer = MapVisualizer()
# showing all trips from and to the pole can make the map messy
show_poles = False
i = 0
for path in df.groupby(by='TripId')['Position'].apply(list):
    # Mark Beginning and End
    folium.CircleMarker(location=path[0], radius=5, color='green', weight=1, fill=True, tooltip=f"Begin {i}")\
        .add_to(visualizer.map)
    folium.CircleMarker(location=path[-1], radius=5, color='red', weight=1, fill=True, tooltip=f"End {i}")\
        .add_to(visualizer.map)

    if show_poles:
        path.insert(0,(90,0))
        path.append((90,0))
    
    i += 1

    visualizer.add_route(path)

visualizer.map

In [ ]:
# Save map (better performance when viewing)
visualizer.save_map("map.html")

## Visualizing one trip with tooltips

In [ ]:
df_single = df.query(f"TripId == 1")

m = get_route_map(df_single, include_home=True)
m